# Classification on MAGIC Gamma Telescope Data Set

### importing libraries

In [1]:
# Data processing
import pandas as pd
import numpy as np

# Data visualization
from pandas_profiling import ProfileReport
import matplotlib as mpl 
#mpl.use('agg')
import matplotlib.pyplot as plt 
import seaborn as sns

# Model and performance
from sklearn import preprocessing
from sklearn.decomposition import PCA
from sklearn.model_selection import train_test_split
from sklearn.model_selection import StratifiedKFold
from sklearn.neighbors import KNeighborsClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.tree import DecisionTreeClassifier
from sklearn import svm
from sklearn import tree
from sklearn import metrics

# Oversampling and under sampling
from imblearn.over_sampling import RandomOverSampler, SMOTE
from imblearn.under_sampling import RandomUnderSampler, NearMiss
from collections import Counter

import os 

### Input Arguments

In [2]:
# select the sampling technique
sampling = 'oversampling'
# choose whether to perform normalization
normalization = True
# set the random seed
random_seed = 42
# choose whether to perform PCA
apply_PCA = True
# variance for the PCA
variance = 0.95
# output directory
if apply_PCA == True:
    output_dir = f'output_PCA_{sampling}'
else:
    output_dir = f'output_{sampling}'



### Useful functions

In [3]:
def ROC_analysis(classifier, val_data, val_y, classifier_name, output_dir):
    
    # predict the class probabilities for all data in validation set
    pred_prob = classifier.predict_proba(val_data)
    pred_prob = pred_prob[:, 0]
    
    # convert validation true labels in binary arrays with 1 in place of 'g' and 0 in place of 'h'
    val_mask = val_y == 'g'
    val_labels = pd.DataFrame(np.zeros_like(val_y))
    val_labels.iloc[val_mask] = 1
    val_labels = val_labels.values.tolist()
    
    fpr = dict()
    tpr = dict()
    roc_auc = dict()    
    for i in range(2):
        fpr[i], tpr[i], tresh = metrics.roc_curve(np.array(val_labels), pred_prob)
        #fpr[i], tpr[i], tresh = roc_curve(y_test, y_pred, pos_label="g" )
        roc_auc[i] = metrics.auc(fpr[i], tpr[i])
        
    index = None
    for x in tresh:
        if x < 0.2 and index == None: 
            index = list(tresh).index(x)
    #print(index)
    #print("x",fpr[0])
    #print("y",tpr[0])
    
    plt.figure(figsize=(12, 10))
    lw = 3
    plt.plot(fpr[0], tpr[0], color='darkorange',
             lw=lw, label='ROC curve (area = %0.2f)' % roc_auc[1])
    plt.plot([0, 1], [0, 1], color='navy', lw=lw, linestyle='--')
    plt.axvline(  list(fpr[0])[index],    color='black', lw=lw)
    plt.xlim([0.0, 1.0])
    plt.ylim([0.0, 1.05])
    plt.xlabel('False Positive Rate')
    plt.ylabel('True Positive Rate')
    plt.title('Receiver Operating Characteristic curve')
    plt.legend(loc="lower right")
    if output_dir is not None:
        plt.savefig(f'{output_dir}/{classifier_name}_{sampling}_ROC.svg', format = 'svg' )
    plt.show()


def train(train_data, train_y, val_data, val_y, classifier, classifier_name, confusion_matrix_plot = True, colormap = plt.cm.Blues, ROC = False, output_dir = None):
     # training 
    classifier.fit(train_data, train_y)
        
    # inference on validation set
    y_pred = classifier.predict(val_data)
        
    # convert predicted labels, and validation true labels in binary arrays with 1 in place of 'g' and 0 in place of 'h'    
    pred_mask = y_pred == 'g'
    pred = pd.DataFrame(np.zeros_like(y_pred))
    pred.iloc[pred_mask] = 1
    pred = pred.values.tolist()
        
    val_mask = val_y == 'g'
    val_labels = pd.DataFrame(np.zeros_like(val_y))
    val_labels.iloc[val_mask] = 1
    val_labels = val_labels.values.tolist()
        
    # compute metrics
    acc = metrics.accuracy_score(val_y, y_pred)
    f1 = metrics.f1_score(val_y, y_pred,pos_label="g")
    auc = metrics.roc_auc_score(val_labels, pred)
    
    print("Accuracy: ",acc)
    print("F1-score: ",f1)
    print("Auc: ",auc, '\n')
  
    conf_mat = metrics.confusion_matrix(y_true=val_y, y_pred=y_pred)
    print('Confusion matrix:\n', conf_mat, '\n')
    if confusion_matrix_plot == True:
        label = ['G', 'B']
        fig = plt.figure(figsize=(10, 10))
        ax = fig.add_subplot(111)
        cax = ax.matshow(conf_mat, cmap=colormap)
        fig.colorbar(cax)
        ax.set_xticks([0, 1])
        ax.set_xticklabels(label)
        ax.set_yticks([0, 1])
        ax.set_yticklabels(label)
        plt.xlabel('Predicted')
        plt.ylabel('Expected')
        plt.title('Confusion Matrix')
        if output_dir is not None:
            plt.savefig(f'{output_dir}/{classifier_name}_{sampling}_ConfusionMatrix.svg', format = 'svg' )
        plt.show()
        
    if ROC == True:
        ROC_analysis(classifier, val_data, val_y, classifier_name, output_dir)
    
    return acc, f1, auc

## Data Exploration, Cleaning and Visualization

### Reading data

In [4]:
# Datafram reading and columns' name definition
df = pd.read_csv('https://archive.ics.uci.edu/ml/machine-learning-databases/magic/magic04.data',header=None)
df.columns = ['1.fLength','2.fWidth','3.fSize','4.fConc','5.fConc','6.fAsym','7.fM3Long','8.fM3Trans','9.fAlpha', '10.fDist','11. class']

# descriptive statistics about dataset distribution
df.describe()

1.fLength      2.fWidth       3.fSize       4.fConc       5.fConc  \
count  19020.000000  19020.000000  19020.000000  19020.000000  19020.000000   
mean      53.250154     22.180966      2.825017      0.380327      0.214657   
std       42.364855     18.346056      0.472599      0.182813      0.110511   
min        4.283500      0.000000      1.941300      0.013100      0.000300   
25%       24.336000     11.863800      2.477100      0.235800      0.128475   
50%       37.147700     17.139900      2.739600      0.354150      0.196500   
75%       70.122175     24.739475      3.101600      0.503700      0.285225   
max      334.177000    256.382000      5.323300      0.893000      0.675200   

            6.fAsym     7.fM3Long    8.fM3Trans      9.fAlpha      10.fDist  
count  19020.000000  19020.000000  19020.000000  19020.000000  19020.000000  
mean      -4.331745     10.545545      0.249726     27.645707    193.818026  
std       59.206062     51.000118     20.827439     26.103621     74.731787  
min     -457.916100   -331.780000   -205.894700      0.000000      1.282600  
25%      -20.586550    -12.842775    -10.849375      5.547925    142.492250  
50%        4.013050     15.314100      0.666200     17.679500    191.851450  
75%       24.063700     35.837800     10.946425     45.883550    240.563825  
max      575.240700    238.321000    179.851000     90.000000    495.561000

**Data Exploration**

In [5]:
# exploratory data analysis
report = ProfileReport(df, title="", html={'style': {'full_width': True}}, sort=None)
report

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

### Removing duplicates

In [6]:
# removing duplicates 
no_copy_df = df.drop_duplicates(subset=['1.fLength','2.fWidth','3.fSize','4.fConc','5.fConc',
                                        '6.fAsym','7.fM3Long','8.fM3Trans','9.fAlpha', '10.fDist','11. class'] ,
                                keep='first', inplace=False)

print(f'number of records in the dataset: {df.shape[0]}')
print(f'number of records in the dataset after removing duplicates: {no_copy_df.shape[0]}')

number of records in the dataset: 19020
number of records in the dataset after removing duplicates: 18905


### Correlation Analysis

In [7]:
# Spearman rank correlation
no_copy_df.corr(method = 'spearman')

1.fLength  2.fWidth   3.fSize   4.fConc   5.fConc   6.fAsym  \
1.fLength    1.000000  0.753027  0.833883 -0.828252 -0.803920 -0.096928   
2.fWidth     0.753027  1.000000  0.838866 -0.853962 -0.831018 -0.096904   
3.fSize      0.833883  0.838866  1.000000 -0.911982 -0.884749 -0.032656   
4.fConc     -0.828252 -0.853962 -0.911982  1.000000  0.986214  0.011588   
5.fConc     -0.803920 -0.831018 -0.884749  0.986214  1.000000  0.001990   
6.fAsym     -0.096928 -0.096904 -0.032656  0.011588  0.001990  1.000000   
7.fM3Long    0.299570  0.210615  0.326728 -0.317768 -0.310281  0.327598   
8.fM3Trans   0.004712  0.013989  0.011610 -0.011899 -0.011323 -0.005073   
9.fAlpha    -0.253661 -0.201025 -0.289884  0.288911  0.282322 -0.074574   
10.fDist     0.480444  0.377587  0.422345 -0.352152 -0.335467 -0.155455   

            7.fM3Long  8.fM3Trans  9.fAlpha  10.fDist  
1.fLength    0.299570    0.004712 -0.253661  0.480444  
2.fWidth     0.210615    0.013989 -0.201025  0.377587  
3.fSize      0.326728    0.011610 -0.289884  0.422345  
4.fConc     -0.317768   -0.011899  0.288911 -0.352152  
5.fConc     -0.310281   -0.011323  0.282322 -0.335467  
6.fAsym      0.327598   -0.005073 -0.074574 -0.155455  
7.fM3Long    1.000000   -0.000760 -0.257922  0.194205  
8.fM3Trans  -0.000760    1.000000 -0.000193  0.006216  
9.fAlpha    -0.257922   -0.000193  1.000000 -0.277800  
10.fDist     0.194205    0.006216 -0.277800  1.000000

**Pairwise features correlation plots**

In [ ]:
# plot pairwise correlation
sns.pairplot(no_copy_df, hue="11. class", markers=['o','*'] )
#plt.savefig(f'{output_dir}/pairwise_correlation.eps', format = 'eps' )
plt.savefig(f'{output_dir}/pairwise_correlation.jpg', format = 'jpg' )
plt.show()

**Removal of highly correlated features**

In [ ]:
# remove column 5 because it is reduntant respect to column 4
cleaned_df = no_copy_df.drop(columns=['5.fConc'])

# separate feature and labels
features = cleaned_df.iloc[:,:9]
labels = cleaned_df.iloc[:,9]

### Data visualization

In [ ]:
# create the output directory if it does not already exists
if not os.path.exists(output_dir):
    os.makedirs(output_dir)

# box plot of the features
fig = plt.figure(figsize=(10, 10))
green_diamond = dict(markerfacecolor='g', marker='D')
plt.boxplot(features, flierprops=green_diamond)
plt.title('Features box plots')
plt.savefig(f'{output_dir}/features_box_plot.svg', format = 'svg' )
plt.show()

# checking if the dataset is balanced
print(f'number of records after removing duplicates: {len(labels)}')
print(f'number of records per class after removing duplicates: {sorted(Counter(labels).items())}')

# bar plot of the number of records for each class 
fig = plt.figure(figsize=(10, 10))
sns.set_theme(style="whitegrid")
sns.countplot(x=labels)
plt.savefig(f'{output_dir}/Dataset_class_distribution.svg', format = 'svg' )
plt.show()

### Train/Test split

In [ ]:
# split data and labels in train and test
X_train, X_test, y_train, y_test = train_test_split(features, labels, test_size=0.2, random_state=random_seed)

# checking if the train set is balanced
print(f'number of records in train set: {len(y_train)}')
print(f'number of records per class in train_set: {sorted(Counter(y_train).items())}')

# checking if the test set is balanced
print(f'number of records in test set: {len(y_test)}')
print(f'number of records per class in test_set: {sorted(Counter(y_test).items())}')

# Classifier Selection

## Data Preprocessing, Models training and performance evaluation

### KNN training and vaidation

In [ ]:
pca_full = PCA()
pca_full.fit(norm_data)

print("NUMBER OF COMPONENTS:" ,len(pca_full.explained_variance_ratio_))
#print(pca_full.explained_variance_ratio_)
#print(np.cumsum(pca_full.explained_variance_ratio_))

tickes = []
for x in range(len(pca_full.explained_variance_ratio_)):
    tickes.append("PC{}".format(x+1))

fig = plt.figure(figsize=[5,5])
plt.bar( range(len(pca_full.explained_variance_ratio_)) , \
        pca_full.explained_variance_ratio_, \
        tick_label = range(len(pca_full.explained_variance_ratio_)) )
plt.plot( range(len(pca_full.explained_variance_ratio_)),\
        np.cumsum(pca_full.explained_variance_ratio_),c="r")
plt.title('Explained variance by each PC and cumulativa explained variance')
plt.xlabel('Principla components')
plt.ylabel('Variance percentage')
plt.xticks(np.arange(61),tickes)
plt.grid()

In [ ]:
# instantiate object to perform k-fold cross validation
kfold = StratifiedKFold(n_splits=5, shuffle=True, random_state=random_seed)

# lists to collect the mean of the metrics for all the train/validation splits as K varies
knn_acc_results = {}
knn_f1_results = {}
knn_auc_results = {}

# different values of K for KNN
for i, K in enumerate([1,3,5,7,15]):            
    # Classifier initialization
    print(f"K-Nearest-Neighbors classifier with K={K}")
    clf= KNeighborsClassifier(K)
    clf_name = 'KNN classifier'
    
    # lists to collect the metrics computed considering all the k possible train-validation splits (according to k-fold cross validation)
    accs = []
    f1s =[]
    aucs = []
    
    # K-fold cross validation
    for j, (train_idx, test_idx) in enumerate(kfold.split(X_train, y_train)):
        train_X, val_X = X_train.iloc[train_idx,:], X_train.iloc[test_idx,:]
        train_y, val_y = y_train.iloc[train_idx], y_train.iloc[test_idx]
        
        # check train and validation split size and composition
        print(f'number of records in train split: {len(train_y)}')
        print(f'number of records per class in train split: {sorted(Counter(train_y).items())}\n')
        
        print(f'number of records in validation split: {len(val_y)}')
        print(f'number of records per class in validation split: {sorted(Counter(val_y).items())}\n')
        
        # perform the sampling to make the train set balance
        if sampling == 'oversampling':
            # Randomly over sample the minority class
            ros = RandomOverSampler(random_state=random_seed)
            s_train_X, s_train_y= ros.fit_resample(train_X, train_y)

        elif sampling == 'undersampling':
            # Randomly under sample the majority class
            rus = RandomUnderSampler(random_state=random_seed)
            s_train_X, s_train_y= rus.fit_resample(train_X, train_y)
        
        # Check the number of records in train split after sampling (only at the first iteration)
        if i == 0 and j == 0:
            sns.set_theme(style="whitegrid")
            sns.countplot(x=train_y).set(title=f'Train split Class distribution')
            plt.savefig(f'{output_dir}/Train_split_class_distr.svg', format = 'svg' )
            plt.show()
            
            sns.set_theme(style="whitegrid")
            sns.countplot(x=s_train_y).set(title=f'Train split Class distribution after {sampling}')
            plt.savefig(f'{output_dir}/Train_split_class_distr_postSampl.svg', format = 'svg' )
            plt.show()
            print(f'number of records in train split after random {sampling}: {len(s_train_y)}')
            print(f'number of records per class in train split after random {sampling}: {sorted(Counter(s_train_y).items())}\n')  
        
        # data normalization
        scaler = preprocessing.MinMaxScaler()
        scaler.fit(s_train_X)
        train_data = scaler.transform(s_train_X)
        val_data = scaler.transform(val_X)
        
        # Plot the variance eplained by each principal components and the cumulative variance (only at the first iteration)
        if i == 0 and j == 0 and apply_PCA == True:
            # Pareto chart plot    
            pca_full = PCA()
            pca_full.fit(train_data)

            print("NUMBER OF COMPONENTS:" ,len(pca_full.explained_variance_ratio_))
            print(pca_full.explained_variance_ratio_)
            print(np.cumsum(pca_full.explained_variance_ratio_))

            tickes = []
            for x in range(len(pca_full.explained_variance_ratio_)):
                tickes.append("PC{}".format(x+1))

            fig = plt.figure(figsize=[10,5])
            plt.grid()
            plt.bar( range(len(pca_full.explained_variance_ratio_)) ,\
                    pca_full.explained_variance_ratio_,\
                    tick_label = range(len(pca_full.explained_variance_ratio_)) )
            plt.plot( range(len(pca_full.explained_variance_ratio_)),\
                     np.cumsum(pca_full.explained_variance_ratio_),c="r")
            plt.grid()
            plt.title('Explained variance by each PC and cumulativa explained variance')
            plt.xlabel('Principla components')
            plt.ylabel('Variance percentage')
            plt.xticks(np.arange(9),tickes)
            plt.savefig(f'{output_dir}/PC_variance.eps', format='eps')
            plt.show()
        
        
        # PCA
        if apply_PCA == True:
            print(f'number of features: {train_data.shape[1]}')
            pca = PCA(n_components=variance, svd_solver='full')
            pca.fit(train_data)
            train_data = pca.transform(train_data)
            val_data = pca.transform(val_data)
            print(f'number of features after PCA: {train_data.shape[1]}')
        
        # training 
        acc, f1, auc = train(train_data, s_train_y, val_data, val_y, clf, clf_name, confusion_matrix_plot = False, ROC = False)
        
        # collect metrics
        accs.append(acc)
        f1s.append(f1)
        aucs.append(auc)
    
    # mean of the metrics computed as the train/validation split changes
    acc_mean = np.mean(accs)
    f1_mean = np.mean(f1s)
    auc_mean = np.mean(aucs)
    
    
    knn_acc_results[K] = acc_mean
    knn_f1_results[K] = f1_mean
    knn_auc_results[K] = auc_mean

print("Accuracy : ",knn_acc_results)
print("F1 score : ",knn_f1_results)
print("AUC score : ",knn_auc_results)

# print the configuration that returns the highest f1 value
best_param = max(knn_f1_results, key = knn_f1_results.get)
print(f'the best KNN parameters configuration is K={best_param} with f1={knn_f1_results[best_param]}')

### Decision Tree training and validation

In [ ]:
# instantiate object to perform k-fold cross validation
kfold = StratifiedKFold(n_splits=5, shuffle=True, random_state=random_seed)

# lists to collect the mean of the metrics for all the train/validation splits as the max depth of the decision tree varies
tree_acc_results = {}
tree_f1_results = {}
tree_auc_results = {}

# different values of max_depth for decision tree
for i, d in enumerate([5,10,50, 100]):            
    # Classifier initialization
    print(f"Decision Tree with max_depth = {d}")
    clf = DecisionTreeClassifier(max_depth=d)
    clf_name = 'Decision Tree classifier'
    
    # lists to collect the metrics computed considering all the k possible train-validation splits (according to k-fold cross validation)
    accs = []
    f1s =[]
    aucs = []
    
    # K-fold cross validation
    for j, (train_idx, test_idx) in enumerate(kfold.split(X_train, y_train)):
        train_X, val_X = X_train.iloc[train_idx,:], X_train.iloc[test_idx,:]
        train_y, val_y = y_train.iloc[train_idx], y_train.iloc[test_idx]
        
        # check train and validation split size and composition
        print(f'number of records in train split: {len(train_y)}')
        print(f'number of records per class in train split: {sorted(Counter(train_y).items())}\n')
        
        print(f'number of records in validation split: {len(val_y)}')
        print(f'number of records per class in validation split: {sorted(Counter(val_y).items())}\n')
        
        # perform the sampling to make the train set balance
        if sampling == 'oversampling':
            # Randomly over sample the minority class
            ros = RandomOverSampler(random_state=random_seed)
            s_train_X, s_train_y= ros.fit_resample(train_X, train_y)

        elif sampling == 'undersampling':
            # Randomly under sample the majority class
            rus = RandomUnderSampler(random_state=random_seed)
            s_train_X, s_train_y= rus.fit_resample(train_X, train_y)
        
        # Check the number of records in train split after sampling (only at the first iteration)
        if i == 0 and j == 0:
            sns.set_theme(style="whitegrid")
            sns.countplot(x=s_train_y).set(title=f'Class distribution after {sampling}')
            plt.show()
            print(f'number of records in train split after random {sampling}: {len(s_train_y)}')
            print(f'number of records per class in train split after random {sampling}: {sorted(Counter(s_train_y).items())}\n')  
        
        # data normalization
        scaler = preprocessing.MinMaxScaler()
        scaler.fit(s_train_X)
        train_data = scaler.transform(s_train_X)
        val_data = scaler.transform(val_X)
        
        # PCA
        if apply_PCA == True:
            print(f'number of features: {train_data.shape[1]}')
            pca = PCA(n_components=variance, svd_solver='full')
            pca.fit(train_data)
            train_data = pca.transform(train_data)
            val_data = pca.transform(val_data)
            print(f'number of features after PCA: {train_data.shape[1]}')
        
        # training 
        acc, f1, auc = train(train_data, s_train_y, val_data, val_y, clf, clf_name, confusion_matrix_plot = False, ROC = False)
        
        # collect metrics
        accs.append(acc)
        f1s.append(f1)
        aucs.append(auc)
    
    # mean of the metrics computed as the train/validation split changes
    acc_mean = np.mean(accs)
    f1_mean = np.mean(f1s)
    auc_mean = np.mean(aucs)
    
    
    tree_acc_results[d] = acc_mean
    tree_f1_results[d] = f1_mean
    tree_auc_results[d] = auc_mean

print("Accuracy : ",tree_acc_results)
print("F1 score : ",tree_f1_results)
print("AUC score : ",tree_auc_results)

# print the configuration that returns the highest f1 value
best_param = max(tree_f1_results, key = tree_f1_results.get)
print(f'the best Decision Tree parameters configuration is max_depth={best_param} with f1={tree_f1_results[best_param]}')

### Random Forest training and validation

In [ ]:
# instantiate object to perform k-fold cross validation
kfold = StratifiedKFold(n_splits=5, shuffle=True, random_state=random_seed)

# lists to collect the mean of the metrics for all the train/validation splits as the number of estimators in the random forrest varies
rf_acc_results = {}
rf_f1_results = {}
rf_auc_results = {}

# different values of estimators for random forest evaluated
for i, est in enumerate([10,50,100,500,1000]):            
    # Classifier initialization
    print(f"Random Forest with {est} estimators")
    clf= RandomForestClassifier(n_estimators=est)
    clf_name = 'Random Forest classifier'
    
    # lists to collect the metrics computed considering all the k possible train-validation splits (according to k-fold cross validation)
    accs = []
    f1s =[]
    aucs = []
    
    # K-fold cross validation
    for j, (train_idx, test_idx) in enumerate(kfold.split(X_train, y_train)):
        train_X, val_X = X_train.iloc[train_idx,:], X_train.iloc[test_idx,:]
        train_y, val_y = y_train.iloc[train_idx], y_train.iloc[test_idx]
        
        # check train and validation split size and composition
        print(f'number of records in train split: {len(train_y)}')
        print(f'number of records per class in train split: {sorted(Counter(train_y).items())}\n')
        
        print(f'number of records in validation split: {len(val_y)}')
        print(f'number of records per class in validation split: {sorted(Counter(val_y).items())}\n')
        
        # perform the sampling to make the train set balance
        if sampling == 'oversampling':
            # Randomly over sample the minority class
            ros = RandomOverSampler(random_state=random_seed)
            s_train_X, s_train_y= ros.fit_resample(train_X, train_y)

        elif sampling == 'undersampling':
            # Randomly under sample the majority class
            rus = RandomUnderSampler(random_state=random_seed)
            s_train_X, s_train_y= rus.fit_resample(train_X, train_y)
        
        # Check the number of records in train split after sampling (only at the first iteration)
        if i == 0 and j == 0:
            sns.set_theme(style="whitegrid")
            sns.countplot(x=s_train_y).set(title=f'Train set Class distribution after {sampling}')
            plt.show()
            print(f'number of records in train split after random {sampling}: {len(s_train_y)}')
            print(f'number of records per class in train split after random {sampling}: {sorted(Counter(s_train_y).items())}\n')  
        
        # data normalization
        scaler = preprocessing.MinMaxScaler()
        scaler.fit(s_train_X)
        train_data = scaler.transform(s_train_X)
        val_data = scaler.transform(val_X)
        
        # PCA
        if apply_PCA == True:
            print(f'number of features: {train_data.shape[1]}')
            pca = PCA(n_components=variance, svd_solver='full')
            pca.fit(train_data)
            train_data = pca.transform(train_data)
            val_data = pca.transform(val_data)
            print(f'number of features after PCA: {train_data.shape[1]}')
        
        # training 
        acc, f1, auc = train(train_data, s_train_y, val_data, val_y, clf, clf_name, confusion_matrix_plot = False, ROC = False)
        
        # collect metrics
        accs.append(acc)
        f1s.append(f1)
        aucs.append(auc)
    
    # mean of the metrics computed as the train/validation split changes
    acc_mean = np.mean(accs)
    f1_mean = np.mean(f1s)
    auc_mean = np.mean(aucs)
    
    
    rf_acc_results[est] = acc_mean
    rf_f1_results[est] = f1_mean
    rf_auc_results[est] = auc_mean

print("Accuracy : ",rf_acc_results)
print("F1 score : ",rf_f1_results)
print("AUC score : ",rf_auc_results)

# print the configuration that returns the highest f1 value
best_param = max(rf_f1_results, key = rf_f1_results.get)
print(f'the best Random Forest parameters configuration is n_estimators={best_param} with f1={rf_f1_results[best_param]}')

### SVM training and validation

In [ ]:
# instantiate object to perform k-fold cross validation
kfold = StratifiedKFold(n_splits=5, shuffle=True, random_state=random_seed)

# lists to collect the mean of the metrics for all the train/validation splits as C and gamma for the SVM change
svm_acc_results = {}
svm_f1_results = {}
svm_auc_results = {}

# different values of C for SVM
for i, C in enumerate([0.1,1,10,100,1000]):
    # different values of gamma for SVM
    for k, g in enumerate([0.001,0.01,0.1,1,10]):
        # Classifier initialization
        print(f"SVM with C={C} and gamma={g}")
        clf = svm.SVC(C=C,gamma=g,probability = True)
        clf_name = 'SVM classifier'

        # lists to collect the metrics computed considering all the k possible train-validation splits (according to k-fold cross validation)
        accs = []
        f1s =[]
        aucs = []

        # K-fold cross validation
        for j, (train_idx, test_idx) in enumerate(kfold.split(X_train, y_train)):
            train_X, val_X = X_train.iloc[train_idx,:], X_train.iloc[test_idx,:]
            train_y, val_y = y_train.iloc[train_idx], y_train.iloc[test_idx]

            # check train and validation split size and composition
            print(f'number of records in train split: {len(train_y)}')
            print(f'number of records per class in train split: {sorted(Counter(train_y).items())}\n')

            print(f'number of records in validation split: {len(val_y)}')
            print(f'number of records per class in validation split: {sorted(Counter(val_y).items())}\n')

            # perform the sampling to make the train set balance
            if sampling == 'oversampling':
                # Randomly over sample the minority class
                ros = RandomOverSampler(random_state=random_seed)
                s_train_X, s_train_y= ros.fit_resample(train_X, train_y)

            elif sampling == 'undersampling':
                # Randomly under sample the majority class
                rus = RandomUnderSampler(random_state=random_seed)
                s_train_X, s_train_y= rus.fit_resample(train_X, train_y)

            # Check the number of records in train split after sampling (only at the first iteration)
            if i == 0 and k == 0 and j == 0:
                sns.set_theme(style="whitegrid")
                sns.countplot(x=s_train_y).set(title=f'Class distribution after {sampling}')
                plt.show()
                print(f'number of records in train split after random {sampling}: {len(s_train_y)}')
                print(f'number of records per class in train split after random {sampling}: {sorted(Counter(s_train_y).items())}\n')  

            # data normalization
            scaler = preprocessing.MinMaxScaler()
            scaler.fit(s_train_X)
            train_data = scaler.transform(s_train_X)
            val_data = scaler.transform(val_X)
            
            # PCA
            if apply_PCA == True:
                print(f'number of features: {train_data.shape[1]}')
                pca = PCA(n_components=variance, svd_solver='full')
                pca.fit(train_data)
                train_data = pca.transform(train_data)
                val_data = pca.transform(val_data)
                print(f'number of features after PCA: {train_data.shape[1]}')

            # training 
            acc, f1, auc = train(train_data, s_train_y, val_data, val_y, clf, clf_name, confusion_matrix_plot = False, ROC = False)

            # collect metrics
            accs.append(acc)
            f1s.append(f1)
            aucs.append(auc)

        # mean of the metrics computed as the train/validation split changes
        acc_mean = np.mean(accs)
        f1_mean = np.mean(f1s)
        auc_mean = np.mean(aucs)


        svm_acc_results[(C,g)] = acc_mean
        svm_f1_results[(C,g)] = f1_mean
        svm_auc_results[(C,g)] = auc_mean

print("Accuracy : ",svm_acc_results)
print("F1 score : ",svm_f1_results)
print("AUC score : ",svm_auc_results)

# print the configuration that returns the highest f1 value
best_param = max(svm_f1_results, key = svm_f1_results.get)
print(f'the best SVM parameters configuration is C={best_param[0]} , gamma={best_param[1]} with f1={svm_f1_results[best_param]}')

## Models test

### KNN Test

In [ ]:
# best KNN initialization
clf= KNeighborsClassifier(15) 
clf_name = 'KNN classifier'

# perform the sampling to make the train set balance
if sampling == 'oversampling':
    # Randomly over sample the minority class
    ros = RandomOverSampler(random_state=random_seed)
    s_X_train, s_y_train= ros.fit_resample(X_train, y_train)

elif sampling == 'undersampling':
    # Randomly under sample the majority class
    rus = RandomUnderSampler(random_state=random_seed)
    s_X_train, s_y_train= rus.fit_resample(X_train, y_train)

sns.set_theme(style="whitegrid")
sns.countplot(x=y_train).set(title=f'Train set Class distribution')
plt.savefig(f'{output_dir}/Train_set_class_distr.svg', format = 'svg' )
plt.show()
            
sns.set_theme(style="whitegrid")
sns.countplot(x=s_y_train).set(title=f'Train set Class distribution after {sampling}')
plt.savefig(f'{output_dir}/Train_set_class_distr_postSampl.svg', format = 'svg' )
plt.show()    

# data normalization
scaler = preprocessing.MinMaxScaler()
scaler.fit(s_X_train)
train_data = scaler.transform(s_X_train)
test_data = scaler.transform(X_test)

# PCA
if apply_PCA == True:
    pca = PCA(n_components=variance, svd_solver='full')
    pca.fit(train_data)
    train_data = pca.transform(train_data)
    test_data = pca.transform(test_data)
    

# train the model on the entire train set and test it on the test set
test_acc, test_f1, test_auc = train(train_data, s_y_train, test_data, y_test, clf, clf_name, confusion_matrix_plot = True, ROC = True, output_dir = output_dir)
print(test_acc, test_f1, test_auc)

### Decision Tree Test

In [ ]:
# best Decision Tree initialization
clf = DecisionTreeClassifier(max_depth=10)
clf_name = 'Decision Tree classifier'

# perform the sampling to make the train set balance
if sampling == 'oversampling':
    # Randomly over sample the minority class
    ros = RandomOverSampler(random_state=random_seed)
    s_X_train, s_y_train= ros.fit_resample(X_train, y_train)

elif sampling == 'undersampling':
    # Randomly under sample the majority class
    rus = RandomUnderSampler(random_state=random_seed)
    s_X_train, s_y_train= rus.fit_resample(X_train, y_train)

# data normalization
scaler = preprocessing.MinMaxScaler()
scaler.fit(s_X_train)
train_data = scaler.transform(s_X_train)
test_data = scaler.transform(X_test)

# PCA
if apply_PCA == True:
    pca = PCA(n_components=variance, svd_solver='full')
    pca.fit(train_data)
    train_data = pca.transform(train_data)
    test_data = pca.transform(test_data)

# train the model on the entire train set and test it on the test set
test_acc, test_f1, test_auc = train(train_data, s_y_train, test_data, y_test, clf, clf_name, confusion_matrix_plot = True, colormap = plt.cm.Greens, ROC = True, output_dir = output_dir)
print(test_acc, test_f1, test_auc)

### Random Forest Test

In [ ]:
# best Random Forest initialization
clf= RandomForestClassifier(n_estimators=100) 
clf_name = 'Random Forest classifier'

# perform the sampling to make the train set balance
if sampling == 'oversampling':
    # Randomly over sample the minority class
    ros = RandomOverSampler(random_state=random_seed)
    s_X_train, s_y_train= ros.fit_resample(X_train, y_train)

elif sampling == 'undersampling':
    # Randomly under sample the majority class
    rus = RandomUnderSampler(random_state=random_seed)
    s_X_train, s_y_train= rus.fit_resample(X_train, y_train)

# data normalization
scaler = preprocessing.MinMaxScaler()
scaler.fit(s_X_train)
train_data = scaler.transform(s_X_train)
test_data = scaler.transform(X_test)

# PCA
if apply_PCA == True:
    pca = PCA(n_components=variance, svd_solver='full')
    pca.fit(train_data)
    train_data = pca.transform(train_data)
    test_data = pca.transform(test_data)

# train the model on the entire train set and test it on the test set
test_acc, test_f1, test_auc = train(train_data, s_y_train, test_data, y_test, clf, clf_name, confusion_matrix_plot = True, colormap = plt.cm.Reds, ROC = True, output_dir = output_dir)
print(test_acc, test_f1, test_auc)

### SVM Test

In [ ]:
# best SVM initialization
clf = svm.SVC(C=10,gamma=10,probability = True)
clf_name = 'SVM classifier'

# perform the sampling to make the train set balance
if sampling == 'oversampling':
    # Randomly over sample the minority class
    ros = RandomOverSampler(random_state=random_seed)
    s_X_train, s_y_train= ros.fit_resample(X_train, y_train)

elif sampling == 'undersampling':
    # Randomly under sample the majority class
    rus = RandomUnderSampler(random_state=random_seed)
    s_X_train, s_y_train= rus.fit_resample(X_train, y_train)

# data normalization
scaler = preprocessing.MinMaxScaler()
scaler.fit(s_X_train)
train_data = scaler.transform(s_X_train)
test_data = scaler.transform(X_test)

# PCA
if apply_PCA == True:
    pca = PCA(n_components=variance, svd_solver='full')
    pca.fit(train_data)
    train_data = pca.transform(train_data)
    test_data = pca.transform(test_data)

# train the model on the entire train set and test it on the test set
test_acc, test_f1, test_auc = train(train_data, s_y_train, test_data, y_test, clf, clf_name, confusion_matrix_plot = True, colormap = plt.cm.Oranges, ROC = True, output_dir = output_dir)
print(test_acc, test_f1, test_auc)